In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split
import numpy as np
from sklearn.externals import joblib
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity


def get_product_from_index(index,customer_data_featured):
    return customer_data_featured.loc[customer_data_featured.index == index,'Product'].iloc[0]

#### Function to get recommended products
def get_similar_products(customer,cosine_sim):
    cust_index = customer.index.values[0]
    similar_products = list(enumerate(cosine_sim[cust_index])) 
    return similar_products

#### Function to get similar customers
def get_similar_customers(sorted_similar_products,customer_data_featured):
    cust_list = []
    j = 0
    for element in sorted_similar_products:
        cust = get_cust_from_index(element[0],customer_data_featured)
        cust_list.append(cust)
        j = j+1
        if j>=5:
            break
    return cust_list
#Categorizing total amount and total number of transaction for each customer.
def categorize_txn(customer_data_featured):
    first_q_totalamt = customer_data_featured.TotalAmount.quantile(0.2)
    second_q_totalamt = customer_data_featured.TotalAmount.quantile(0.4)
    third_q_totalamt = customer_data_featured.TotalAmount.quantile(0.6)
    fourth_q_totalamt = customer_data_featured.TotalAmount.quantile(0.8)
    
    first_q_noOfTxn = customer_data_featured.NumberOfTransactions.quantile(0.2)
    second_q_noOfTxn = customer_data_featured.NumberOfTransactions.quantile(0.4)
    third_q_noOfTxn = customer_data_featured.NumberOfTransactions.quantile(0.6)
    fourth_q_noOfTxn = customer_data_featured.NumberOfTransactions.quantile(0.8) 
    
    customer_data_featured.loc[customer_data_featured.TotalAmount <= first_q_totalamt,'Amt_cat']="First"
    customer_data_featured.loc[(customer_data_featured.TotalAmount > first_q_totalamt) &  (customer_data_featured.TotalAmount <= second_q_totalamt),'Amt_cat']="Second"
    customer_data_featured.loc[(customer_data_featured.TotalAmount > second_q_totalamt) &  (customer_data_featured.TotalAmount <= third_q_totalamt),'Amt_cat']="Third"
    customer_data_featured.loc[(customer_data_featured.TotalAmount > third_q_totalamt) &  (customer_data_featured.TotalAmount <= fourth_q_totalamt),'Amt_cat']="Fourth"
    customer_data_featured.loc[customer_data_featured.TotalAmount > fourth_q_totalamt,'Amt_cat']="Fifth"
    
    customer_data_featured.loc[customer_data_featured.NumberOfTransactions <= first_q_noOfTxn,'txn_cat']="First"
    customer_data_featured.loc[(customer_data_featured.NumberOfTransactions > first_q_noOfTxn) &  (customer_data_featured.NumberOfTransactions <= first_q_noOfTxn),'txn_cat']="Second"
    customer_data_featured.loc[(customer_data_featured.NumberOfTransactions > first_q_noOfTxn) &  (customer_data_featured.NumberOfTransactions <= first_q_noOfTxn),'txn_cat']="Third"
    customer_data_featured.loc[(customer_data_featured.NumberOfTransactions > first_q_noOfTxn) &  (customer_data_featured.NumberOfTransactions <= first_q_noOfTxn),'txn_cat']="Fourth"
    customer_data_featured.loc[customer_data_featured.NumberOfTransactions > first_q_noOfTxn,'txn_cat']="Fifth"
    
    customer_data_featured.drop(['NumberOfTransactions','TotalAmount'], inplace=True, axis=1)
    customer_data_featured.rename(columns={'Amt_cat':'TotalAmount'},inplace=True)
    customer_data_featured.rename(columns={'txn_cat':'NumberOfTransactions'},inplace=True)
    
    #print(customer_data_featured[['NumberOfTransactions','TotalAmount']])
    return customer_data_featured


#### KYCS is not a product so we have to remove it from product list against all custmers.
def remove_KYCS(input):
    removal_str = 'KYCS'
    sep = ", "

    prod_list = (sep.join([ i for i in input.split(sep) if i != removal_str ]))
    if len(prod_list) == 0:
        prod_list= np.nan
    return prod_list

#### Function to get a list of top 3 recommended products

def top_3_recommended_prod(customer_availaing_products,recommended):
    customer_availaing_products = [x.upper() for x in customer_availaing_products]
    availaing_products_set  = set(customer_availaing_products)
    recommended_set = set(recommended)
    difference = recommended_set - availaing_products_set
    top_3 = list(difference)[:3]
    return top_3

def get_recommendation(cind,input_feature_list):
    cind = int(cind)
    #Reading data from CSV to a dataframe
    customer_data = pd.read_csv("cust_360.csv")
    #Getting the input'cu
    #print("1")
    rm = customer_data.loc[customer_data.CIND == cind, 'RM'].iloc[0]
    #print("RM:  ",rm)
    
    customer_data.rename(columns={'Sources':'Product'},inplace=True)
    #Removing the KYCS sourcses and adding a column 'Product'
    customer_data['Product'] = customer_data['Product'].apply(remove_KYCS)
    customer_data.loc[(customer_data.CIND==cind) & (customer_data.Product.isnull()),['Product']]='NA'

    #Removing rows from the dataframe where source value in NaN
    customer_data.dropna(subset=['Product'],inplace=True)
    
    #Adding index column
    customer_data = customer_data.reset_index()
    customer_data['index'] = customer_data.index
    
    #Keeping only important features
    customer_data_featured = customer_data[['index','CIND','Country','LOB','NumberOfTransactions','Product','TotalAmount']]
    
    #Categorizing Total amount and number of transactions
    customer_data_featured = categorize_txn(customer_data_featured)

    #Default features if no feature is selected by end user
    deafaultFeatures = ['Country', 'LOB','NumberOfTransactions','TotalAmount']
        
    #filling all the NaN values with blank string in the dataframe.
    for feature in deafaultFeatures:
        customer_data_featured[feature] = customer_data_featured[feature].fillna('') #filling all NaNs with blank string
    print("Feature length : ",len(input_feature_list))
    if(len(input_feature_list)>0):
        customer_data_featured['combined_features'] = customer_data_featured[input_feature_list].apply(lambda row: ' '.join(row.values.astype(str)), axis=1)
    else:
        customer_data_featured['combined_features'] = customer_data_featured[deafaultFeatures].apply(lambda row: ' '.join(row.values.astype(str)), axis=1)
    #Feeding these strings to a CountVectorizer() object for getting the count matrix.
    print(customer_data_featured[['CIND','combined_features']])
    cv = CountVectorizer() #creating new CountVectorizer() object
    count_matrix = cv.fit_transform(customer_data_featured["combined_features"])
    
    #Obtain the cosine similarity matrix from the count matrix.
    cosine_sim = cosine_similarity(count_matrix)
    selected_customer = customer_data_featured.loc[customer_data_featured.CIND==cind]
   
    #customer_availaing_products = customer_using_prods(selected_customer)
    customer_products = selected_customer.Product.values[0]
    customer_availaing_products = [y.strip() for y in customer_products.split(",")]
    #Get similar products
    cust_index = selected_customer.index.values[0]
    similar_products = list(enumerate(cosine_sim[cust_index]))
    sorted_similar_products = sorted(similar_products,key=lambda x:x[1],reverse=True)[1:]
    #print(sorted_similar_products)
    #Recommending top 3 products and getting top 5 similar customers
    recommended=[]    
    for element in sorted_similar_products:
        recommended.extend([x.strip() for x in get_product_from_index(element[0],customer_data_featured).upper().split(",") if x.strip() not in customer_availaing_products and x.strip() not in recommended])
        #print("recommended and length",recommended,len(recommended))
        if len(recommended)>=3:
            break
    top5_similar_cust_list =[]
    for cust_element in sorted_similar_products:
        cust = customer_data_featured[customer_data_featured.index == cust_element[0]]["CIND"].values[0]
        top5_similar_cust_list.append(int(cust))
        if len(top5_similar_cust_list)>=5:
            break

    products = {'RM':rm,'existing':list(customer_availaing_products), 'recommended' : recommended[:3], 'similar_customers' : top5_similar_cust_list[:5]}
    return products

In [2]:
l = get_recommendation("48278647",['TotalAmount'])

D:\Python\Anaconda\lib\site-packages\pandas\core\indexing.py:362: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[key] = _infer_fill_value(value)
D:\Python\Anaconda\lib\site-packages\pandas\core\indexing.py:543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s
D:\Python\Anaconda\lib\site-packages\pandas\core\frame.py:3697: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-v

Feature length :  1
           CIND combined_features
0     102222193            Fourth
1     742139763            Fourth
2     393626152             Fifth
3     482533642             First
4     814527997            Second
5     288472741            Fourth
6      85721694             First
7     950153926             Third
8     478296233             First
9     660384568             First
10    726947825             First
11    170554251            Second
12    100293867             Fifth
13    605307694             Third
14    307135145             First
15    155096807            Fourth
16    100293852             Fifth
17     88289285             First
18    194642226            Second
19    826544171             First
20    356697578             Fifth
21    101077235             Fifth
22    962305459            Fourth
23    308223447            Second
24    345146077            Second
25    493010688            Second
26    100261818             Third
27    653355077             

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:116: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [3]:
l

{'RM': 'Leland Lish  ',
 'existing': ['GPS', 'HCAL', 'WDA'],
 'recommended': ['IMPACT FIN', 'IMPACT TRADES', 'NFOS'],
 'similar_customers': [742139763, 288472741, 155096807, 962305459, 145900279]}

In [4]:
l = get_recommendation("48278647",['Country', 'LOB', 'NumberOfTransactions','TotalAmount'])

D:\Python\Anaconda\lib\site-packages\pandas\core\indexing.py:362: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[key] = _infer_fill_value(value)
D:\Python\Anaconda\lib\site-packages\pandas\core\indexing.py:543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s
D:\Python\Anaconda\lib\site-packages\pandas\core\frame.py:3697: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-v

Feature length :  4
           CIND      combined_features
0     102222193   twn gbm Fifth Fourth
1     742139763   usa gbm Fifth Fourth
2     393626152    usa gbm Fifth Fifth
3     482533642    usa gbm Fifth First
4     814527997   usa gbm Fifth Second
5     288472741   per gbm Fifth Fourth
6      85721694    usa gbm Fifth First
7     950153926    che gbm Fifth Third
8     478296233    usa gbm First First
9     660384568    bmu gbm First First
10    726947825    sgp gbm First First
11    170554251   usa gbm Fifth Second
12    100293867    usa gbm Fifth Fifth
13    605307694    can gbm Fifth Third
14    307135145    usa gbm Fifth First
15    155096807   usa gbm Fifth Fourth
16    100293852    chn gbm Fifth Fifth
17     88289285    usa gbm First First
18    194642226   aus gbm Fifth Second
19    826544171    usa gbm First First
20    356697578    usa gbm Fifth Fifth
21    101077235    gbr gbm Fifth Fifth
22    962305459   usa gbm Fifth Fourth
23    308223447   usa gbm First Second
24   

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:116: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [5]:
l

{'RM': 'Leland Lish  ',
 'existing': ['GPS', 'HCAL', 'WDA'],
 'recommended': ['IMPACT FIN', 'IMPACT TRADES', 'NFOS'],
 'similar_customers': [100249422, 620211130, 621172148, 48278647, 951176459]}

In [6]:
l = get_recommendation("48278647",['TotalAmount'])

D:\Python\Anaconda\lib\site-packages\pandas\core\indexing.py:362: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[key] = _infer_fill_value(value)
D:\Python\Anaconda\lib\site-packages\pandas\core\indexing.py:543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s
D:\Python\Anaconda\lib\site-packages\pandas\core\frame.py:3697: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-v

Feature length :  1
           CIND combined_features
0     102222193            Fourth
1     742139763            Fourth
2     393626152             Fifth
3     482533642             First
4     814527997            Second
5     288472741            Fourth
6      85721694             First
7     950153926             Third
8     478296233             First
9     660384568             First
10    726947825             First
11    170554251            Second
12    100293867             Fifth
13    605307694             Third
14    307135145             First
15    155096807            Fourth
16    100293852             Fifth
17     88289285             First
18    194642226            Second
19    826544171             First
20    356697578             Fifth
21    101077235             Fifth
22    962305459            Fourth
23    308223447            Second
24    345146077            Second
25    493010688            Second
26    100261818             Third
27    653355077             

In [7]:
l

{'RM': 'Leland Lish  ',
 'existing': ['GPS', 'HCAL', 'WDA'],
 'recommended': ['IMPACT FIN', 'IMPACT TRADES', 'NFOS'],
 'similar_customers': [742139763, 288472741, 155096807, 962305459, 145900279]}

In [8]:
l

{'RM': 'Leland Lish  ',
 'existing': ['GPS', 'HCAL', 'WDA'],
 'recommended': ['IMPACT FIN', 'IMPACT TRADES', 'NFOS'],
 'similar_customers': [742139763, 288472741, 155096807, 962305459, 145900279]}

In [9]:
df = pd.read_csv("Cust_360_latest_28082020.csv")
all_cind = df.CIND.values
all_cind = list(map(str,all_cind))
all_cind
len(all_cind)

FileNotFoundError: File b'Cust_360_latest_28082020.csv' does not exist

In [222]:
final = pd.DataFrame(columns=['CIND','Rec','Simcust'])
i = 0
for c in all_cind:
    cind = str(c)
    l = get_recommendation(cind,['Country', 'LOB', 'NumberOfTransactions','TotalAmount'])
    rec_prd = ",".join(l['recommended'])
    sim_cust = ",".join(list(map(str,l['similar_customers'])))
    final.loc[i] = cind, rec_prd,sim_cust
    i = i+1
print(final)

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:116: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:117: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:124: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:117: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:124: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:116: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:117: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:116: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:117: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:124: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:117: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:124: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

...

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:116: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:117: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:124: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:117: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:124: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:116: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:117: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:124: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:117: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:124: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

           CIND                           Rec  \
0     102222193                          HCAL   
1     742139763                  FISC,ADP,WDA   
2     680132382        IMPACT TRADES,FISC,WDA   
3     393626152                   TDA,TRT,GPS   
4     482533642     ADP,IMPACT TRADES,LOAN IQ   
5     121774710        IMPACT TRADES,FISC,WDA   
6      74279905      IMPACT TRADES,FISC,FITEK   
7     762862144        IMPACT TRADES,FISC,WDA   
8     814527997                  FISC,WDA,ADP   
9     288472741                   GPS,DDA,WDA   
10     85721694                 HIE,FITEK,WDA   
11    950153926  IMPACT TRADES,IMPACT FIN,GPS   
12    478296233                  GPS,FISC,DDA   
13    660384568                   GPS,DDA,WDA   
14    100936225      IMPACT TRADES,FISC,FITEK   
15    202001917        IMPACT TRADES,FISC,WDA   
16    726947825                ADP,FISC,FITEK   
17    170554251                       GPS,WDA   
18    100293867                   HIE,GPS,ADP   
19    867682884     

In [13]:
remaining_cind = ["398698993","572804150","100960849","295424879","101132919","99998366","642113491","38426013","100292291","48278647","283185745","236314921","771142133","416187417","155203299","443709148","235037292","448421649","314833612","871288148","192440043","89323824"
]

In [14]:
final = pd.DataFrame(columns=['CIND','Rec','Simcust'])
i = 0
for c in remaining_cind:
    cind = str(c)
    l = get_recommendation(cind,['Country', 'LOB', 'NumberOfTransactions','TotalAmount'])
    rec_prd = ",".join(l['recommended'])
    sim_cust = ",".join(list(map(str,l['similar_customers'])))
    final.loc[i] = cind, rec_prd,sim_cust
    i = i+1
print(final)

1


D:\Python\Anaconda\lib\site-packages\pandas\core\indexing.py:362: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[key] = _infer_fill_value(value)
D:\Python\Anaconda\lib\site-packages\pandas\core\indexing.py:543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s
D:\Python\Anaconda\lib\site-packages\pandas\core\frame.py:3697: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-v

1


D:\Python\Anaconda\lib\site-packages\pandas\core\indexing.py:362: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[key] = _infer_fill_value(value)
D:\Python\Anaconda\lib\site-packages\pandas\core\indexing.py:543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s
D:\Python\Anaconda\lib\site-packages\pandas\core\frame.py:3697: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-v

1


...

D:\Python\Anaconda\lib\site-packages\pandas\core\indexing.py:362: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[key] = _infer_fill_value(value)
D:\Python\Anaconda\lib\site-packages\pandas\core\indexing.py:543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s
D:\Python\Anaconda\lib\site-packages\pandas\core\frame.py:3697: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-v

1


D:\Python\Anaconda\lib\site-packages\pandas\core\indexing.py:362: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[key] = _infer_fill_value(value)
D:\Python\Anaconda\lib\site-packages\pandas\core\indexing.py:543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s
D:\Python\Anaconda\lib\site-packages\pandas\core\frame.py:3697: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-v

         CIND                                     Rec  \
0   398698993           FISC,IMPACT FIN,IMPACT TRADES   
1   572804150                        LOAN IQ,NFOS,PMC   
2   100960849                        LOAN IQ,NFOS,PMC   
3   295424879                        NFOS,DDA,LOAN IQ   
4   101132919    LOAN IQ,TRT,IMPACT FIN,IMPACT TRADES   
5    99998366                        NFOS,DDA,LOAN IQ   
6   642113491                        NFOS,DDA,LOAN IQ   
7    38426013                        NFOS,DDA,LOAN IQ   
8   100292291                        NFOS,DDA,LOAN IQ   
9    48278647  IMPACT FIN,IMPACT TRADES,ADP,FISC,NFOS   
10  283185745  ADP,FISC,IMPACT FIN,IMPACT TRADES,NFOS   
11  236314921                             WDA,GPS,DDA   
12  771142133           LOAN IQ,HIE,IMPACT TRADES,SMT   
13  416187417  ADP,FISC,IMPACT FIN,IMPACT TRADES,NFOS   
14  155203299                        NFOS,DDA,LOAN IQ   
15  443709148                            DTP,NFOS,DDA   
16  235037292                  

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:116: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [15]:
final

CIND                                     Rec  \
0   398698993           FISC,IMPACT FIN,IMPACT TRADES   
1   572804150                        LOAN IQ,NFOS,PMC   
2   100960849                        LOAN IQ,NFOS,PMC   
3   295424879                        NFOS,DDA,LOAN IQ   
4   101132919    LOAN IQ,TRT,IMPACT FIN,IMPACT TRADES   
5    99998366                        NFOS,DDA,LOAN IQ   
6   642113491                        NFOS,DDA,LOAN IQ   
7    38426013                        NFOS,DDA,LOAN IQ   
8   100292291                        NFOS,DDA,LOAN IQ   
9    48278647  IMPACT FIN,IMPACT TRADES,ADP,FISC,NFOS   
10  283185745  ADP,FISC,IMPACT FIN,IMPACT TRADES,NFOS   
11  236314921                             WDA,GPS,DDA   
12  771142133           LOAN IQ,HIE,IMPACT TRADES,SMT   
13  416187417  ADP,FISC,IMPACT FIN,IMPACT TRADES,NFOS   
14  155203299                        NFOS,DDA,LOAN IQ   
15  443709148                            DTP,NFOS,DDA   
16  235037292                        LOAN IQ,NFOS,PMC   
17  448421649                        NFOS,DDA,LOAN IQ   
18  314833612                        NFOS,DDA,LOAN IQ   
19  871288148                        NFOS,DDA,LOAN IQ   
20  192440043                        NFOS,LOAN IQ,SMT   
21   89323824                         WDA,LOAN IQ,HIE   

                                              Simcust  
0    393626152,482533642,814527997,85721694,478296233  
1   100804561,572804150,100958093,838286780,100960849  
2   100804561,572804150,100958093,838286780,100960849  
3   345146077,224436066,461080427,101037762,981384595  
4   963964259,100771557,100297266,101132919,931726603  
5   345146077,224436066,461080427,101037762,981384595  
6   345146077,224436066,461080427,101037762,981384595  
7   345146077,224436066,461080427,101037762,981384595  
8   345146077,224436066,461080427,101037762,981384595  
9     23743137,100249422,620211130,621172148,48278647  
10   393626152,482533642,814527997,85721694,478296233  
11  345146077,224436066,461080427,101037762,981384595  
12  771142133,194642226,100804561,572804150,100958093  
13   393626152,482533642,814527997,85721694,478296233  
14  345146077,224436066,461080427,101037762,981384595  
15  135922499,310456983,179501685,419293815,100301139  
16  100804561,572804150,100958093,838286780,100960849  
17  345146077,224436066,461080427,101037762,981384595  
18  345146077,224436066,461080427,101037762,981384595  
19  345146077,224436066,461080427,101037762,981384595  
20  788937812,325561260,780920326,907379967,788937812  
21   56435356,829663220,433697358,764303071,451605740

In [221]:
final

CIND                        Rec  \
0  102222193                       HCAL   
1  742139763               FISC,ADP,WDA   
2  680132382     IMPACT TRADES,FISC,WDA   
3  393626152                TDA,TRT,GPS   
4  482533642  ADP,IMPACT TRADES,LOAN IQ   
5  121774710     IMPACT TRADES,FISC,WDA   
6   74279905   IMPACT TRADES,FISC,FITEK   
7  762862144     IMPACT TRADES,FISC,WDA   

                                             Simcust  
0   100249422,620211130,621172148,48278647,951176459  
1   155096807,487097742,110193821,245646563,69827604  
2   478296233,88289285,826544171,996234558,187553798  
3  288241051,127435280,112132154,763761513,991609912  
4  308223447,493010688,716207948,754554607,508545026  
5   478296233,88289285,826544171,996234558,187553798  
6  838286780,612735807,237585914,478296233,660384568  
7   478296233,88289285,826544171,996234558,187553798

In [172]:
l = get_recommendation("999911995",['Country', 'LOB', 'NumberOfTransactions'])

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:107: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

In [174]:
df = pd.read_csv("Cust_360_latest_27082020.csv")

In [176]:
all_cind = df.CIND.values
all_cind
cust_list=[]
#all_cind=["999466818","999889615"]
#all_cind=["999911995","999889615"]

#all_cind=["999911995","999889615","999469024","999466818"]
for i in all_cind:
    cust_list.append(str(i))
#print(cust_list)

In [177]:
final = pd.DataFrame(columns=['CIND','Rec'])
i = 0
#df = pd.DataFrame()
for c in cust_list:
    cind = str(c)
    #print(cind)
    #print(type(cind))
    l = get_recommendation(cind,['Country', 'LOB', 'NumberOfTransactions','TotalAmount'])
    rec_prd = ",".join(l['recommended'])
    #sim_cust = ",".join(l['similar_customers'])
    final.loc[i] = cind, rec_prd
    i = i+1
    #df = pd.DataFrame()
    #df['CIND'] = [cind] 
    #df['Rec'] = rec_prd
    #print(df)
    #final.append(df,ignore_index=True)
print(final)

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:107: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:107: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:107: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:107: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:138: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

...

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:138: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:138: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:138: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

           CIND                     Rec
0     999911995            HIE,GPS,NFOS
1     999889615             NFOS,NA,WDA
2     999469024  NFOS,IMPACT TRADES,WDA
3     999466818              NA,WDA,TRT
4     998915735  NFOS,IMPACT TRADES,WDA
5     998752577  IMPACT TRADES,NA,FITEK
6     997832121  NFOS,IMPACT TRADES,WDA
7     997476978            NA,PMC,FITEK
8     996419066    NA,WDA,IMPACT TRADES
9     996379703  NFOS,IMPACT TRADES,WDA
10    996234558              CAL,NA,PMC
11    995779276  NFOS,CAL,IMPACT TRADES
12    995517765             GPS,DDA,WDA
13    995234558  NFOS,IMPACT TRADES,WDA
14    995120291  GPS,NFOS,IMPACT TRADES
15    995099981  GPS,NFOS,IMPACT TRADES
16    994646590              NA,PMC,WDA
17    993369423   NFOS,IMPACT TRADES,NA
18    993165922   NFOS,IMPACT TRADES,NA
19    992156046   NFOS,IMPACT TRADES,NA
20    992031578    IMPACT TRADES,NA,PMC
21    991980091              NA,PMC,WDA
22    991609912  GPS,NFOS,IMPACT TRADES
23    991429115  GPS,NFOS,IMPACT TRADES


D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:141: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [178]:
final

CIND                     Rec
0     999911995            HIE,GPS,NFOS
1     999889615             NFOS,NA,WDA
2     999469024  NFOS,IMPACT TRADES,WDA
3     999466818              NA,WDA,TRT
4     998915735  NFOS,IMPACT TRADES,WDA
5     998752577  IMPACT TRADES,NA,FITEK
6     997832121  NFOS,IMPACT TRADES,WDA
7     997476978            NA,PMC,FITEK
8     996419066    NA,WDA,IMPACT TRADES
9     996379703  NFOS,IMPACT TRADES,WDA
10    996234558              CAL,NA,PMC
11    995779276  NFOS,CAL,IMPACT TRADES
12    995517765             GPS,DDA,WDA
13    995234558  NFOS,IMPACT TRADES,WDA
14    995120291  GPS,NFOS,IMPACT TRADES
15    995099981  GPS,NFOS,IMPACT TRADES
16    994646590              NA,PMC,WDA
17    993369423   NFOS,IMPACT TRADES,NA
18    993165922   NFOS,IMPACT TRADES,NA
19    992156046   NFOS,IMPACT TRADES,NA
20    992031578    IMPACT TRADES,NA,PMC
21    991980091              NA,PMC,WDA
22    991609912  GPS,NFOS,IMPACT TRADES
23    991429115  GPS,NFOS,IMPACT TRADES
24    990726465   NFOS,IMPACT TRADES,NA
25    990599203    NA,GPS,IMPACT TRADES
26    989750447  NFOS,IMPACT TRADES,WDA
27    989527929            HIE,NA,FITEK
28    989424764  NFOS,CAL,IMPACT TRADES
29    989012365            NFOS,NA,FISC
...         ...                     ...
2436   15239029             GPS,DDA,WDA
2437   14186611   GPS,DDA,IMPACT TRADES
2438   14094808       ADP,IMPACT TRADES
2439   13785664             GPS,DDA,WDA
2440   13658243  NFOS,CAL,IMPACT TRADES
2441   13534752            HIE,NFOS,GPS
2442   13212902                 NA,NFOS
2443   13069976            HIE,ADP,NFOS
2444   12986724             GPS,DDA,WDA
2445   12149061            HIE,GPS,NFOS
2446   11735675              NA,GPS,DDA
2447   11082341                DDA,NFOS
2448   10908361            GPS,DDA,NFOS
2449   10060051            GPS,DDA,NFOS
2450    9614720            GPS,DDA,NFOS
2451    9542553            GPS,DDA,NFOS
2452    8522237              NA,GPS,DDA
2453    7898092             NFOS,NA,WDA
2454    7501757              NA,ADP,WDA
2455    6365212   IMPACT TRADES,NA,FISC
2456    5817014            GPS,DDA,NFOS
2457    4957476                      NA
2458    4709534            GPS,DDA,NFOS
2459    4277511            GPS,DDA,NFOS
2460     314802            HIE,DDA,NFOS
2461    1454173             NA,DDA,NFOS
2462    1243915              NA,GPS,WDA
2463    1184440            GPS,DDA,NFOS
2464    1072369            GPS,DDA,NFOS
2465    1034991             HIE,NFOS,NA

[2466 rows x 2 columns]

In [180]:
l = get_recommendation("999889615",['Country', 'LOB', 'NumberOfTransactions'])

D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:107: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:130: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
D:\Python\Anaconda\lib\site-packages\ipykernel_launcher.py:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-

In [181]:
l

{'existing': ['Impact Trades'],
 'recommended': ['NFOS', 'CAL', 'NA'],
 'similar_customers': [999889615, 998752577, 999466818, 997476978, 996419066]}

In [8]:
def multipliers():
  return [lambda x : i * x for i in range(4)]
    
print([m(3) for m in multipliers()])

[9, 9, 9, 9]


In [3]:
a = [lambda x : i * x for i in range(4)]
a

[<function __main__.<listcomp>.<lambda>(x)>,
 <function __main__.<listcomp>.<lambda>(x)>,
 <function __main__.<listcomp>.<lambda>(x)>,
 <function __main__.<listcomp>.<lambda>(x)>]